# Regression model for traffic and air quality prediction in time

This notebook explains and performs the training of two models for predicting a state hours (the number is configurable) in the future.
It defines a clear and simple way of setting up the experimental environnement for machine learning experiment (train/test datasets, evaluation metrics...).
I chose to use sklearn for its ease of use.

In [36]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_absolute_error, r2_score, mean_squared_error
from lightgbm import LGBMRegressor
import plotly.graph_objects as go

Loading the dataset

In [37]:
df=pd.read_pickle("final_dataset.pkl")
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7321 entries, 0 to 7320
Data columns (total 25 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             7321 non-null   object        
 1   hour             7321 non-null   int32         
 2   traffic_z0       7321 non-null   float64       
 3   traffic_z1       7321 non-null   float64       
 4   traffic_z3       7321 non-null   float64       
 5   traffic_z4       7321 non-null   float64       
 6   traffic_z5       7321 non-null   float64       
 7   traffic_z6       7321 non-null   float64       
 8   traffic_z7       7321 non-null   float64       
 9   traffic_z8       7321 non-null   float64       
 10  datetime_hour_x  7321 non-null   datetime64[ns]
 11  station_4        7321 non-null   float64       
 12  station_43       7321 non-null   float64       
 13  station_54       7321 non-null   float64       
 14  station_58       7321 non-null   float64

We will predict both traffic and air quality in the future. Here is the number of hours in the future the prediction will be made.

In [38]:
forecast_h = 12 # Prediction will be made for forecast_h hours in the future

# Predicting traffic

In [39]:
# Identifying the 'traffic_zN' columns
traffic_cols = [c for c in df.columns if c.startswith("traffic_")]

# Creating the target value (value forecast_h hours after) for every traffic area
for col in traffic_cols:
    df[f"target_{col}"] = df[col].shift(-forecast_h)

# This functions add lags (values from previous hours) and rolls (previous rolling means over time windows)
def add_lags_and_rolls(df, cols, lags=[1, 2, 3, 6, 12], rolls=[3, 6, 12]):
    for col in cols:
        for lag in lags:
            df[f"{col}_lag{lag}"] = df[col].shift(lag)
        for w in rolls:
            df[f"{col}_roll{w}"] = df[col].rolling(window=w).mean()
    return df

df = add_lags_and_rolls(df, traffic_cols)
df["dayofweek"] = df["datetime_hour"].dt.dayofweek
df = df.dropna().reset_index(drop=True)

Training of one model per zone

In [40]:
models_traffic = {}
scalers_traffic = {}
for col in traffic_cols:
    # Features : lags/rolling de la zone + temporel
    feature_cols = [c for c in df.columns if c.startswith(f"{col}_") or c in ["hour", "dayofweek"]]
    X = df[feature_cols]
    y = df[f"target_{col}"]

    # Split train/test
    split_idx = int(len(df) * 0.8)
    X_train, X_test = X.iloc[:split_idx], X.iloc[split_idx:]
    y_train, y_test = y.iloc[:split_idx], y.iloc[split_idx:]

    # Normalisation
    scaler = StandardScaler()
    X_train_scaled = scaler.fit_transform(X_train)
    X_test_scaled = scaler.transform(X_test)
    scalers_traffic[col] = scaler

    # Model
    model = LGBMRegressor(n_estimators=300, learning_rate=0.05, random_state=42)
    model.fit(X_train_scaled, y_train)
    models_traffic[col] = model

    # Metrics
    y_pred = model.predict(X_test_scaled)
    mae = mean_absolute_error(y_test, y_pred)
    r2 = r2_score(y_test, y_pred)
    print(f"[TRAFFIC] {col}: MAE = {mae:.2f}, R² = {r2:.3f}")

    fig = go.Figure()
    fig.add_trace(go.Scatter(
        x=df["datetime_hour"].iloc[split_idx:],
        y=y_test,
        mode='lines',
        name='VReal values',
        line=dict(color='blue')
    ))
    fig.add_trace(go.Scatter(
        x=df["datetime_hour"].iloc[split_idx:],
        y=y_pred,
        mode='lines',
        name='Prédictions',
        line=dict(color='red', dash='dash')
    ))
    fig.update_layout(
        title=f"Traffic prediction in ({col}) for +{forecast_h}h",
        xaxis_title="Date",
        yaxis_title="Traffic",
        hovermode="x unified",
        template="plotly_white"
    )
    fig.show()


[TRAFFIC] traffic_z0: MAE = 0.39, R² = 0.273


[TRAFFIC] traffic_z1: MAE = 0.28, R² = 0.641


[TRAFFIC] traffic_z3: MAE = 0.32, R² = 0.716


[TRAFFIC] traffic_z4: MAE = 0.36, R² = 0.041


[TRAFFIC] traffic_z5: MAE = 0.20, R² = 0.540


[TRAFFIC] traffic_z6: MAE = 0.61, R² = 0.694


[TRAFFIC] traffic_z7: MAE = 0.23, R² = 0.749


[TRAFFIC] traffic_z8: MAE = 0.25, R² = 0.727


# Predicting air quality
First with real traffic values. (Later I will use the predicted ones)

In [41]:
# Identify the station cols
station_cols = [c for c in df.columns if c.startswith("station_")]
weather_cols = ["temperature", "wind_u", "wind_v", "precipitation", "is_raining", "humidity", "pressure", "cloud_cover"]
weather_cols = [c for c in weather_cols if c in df.columns]

Creation of the `target column`: this is the value we will try to predict for a given hour. It is either the air quality measured by station 4 in `forecast_h` hours, or the mean of all the measures in `forecast_h` hours. the following cell allows to choose.

In [42]:
# Target: Can be either the mean of all the stations, or one specific station.

# For the mean, uncomment this
#target, target_label = df[station_cols].mean(axis=1), "Average PM10 levels"

# For the station 4, uncomment this
target, target_label = df[['station_4']], "PM10 levels in station 4"

In [43]:
df["air_quality_selected"] = target
df["target_air_quality"] = df["air_quality_selected"].shift(-forecast_h)


# Create Lags/rolling pour la qualité de l'air et la météo
df = add_lags_and_rolls(df, ["air_quality_selected"] + weather_cols)
df = df.dropna().reset_index(drop=True) # By creating lags, we will loose forecast_h rows

"""# Ajout des prédictions de trafic (ou des données réelles)
use_predicted_traffic = True  # Option true/False
 if use_predicted_traffic:
    for col in traffic_cols:
        # Prédire le trafic pour toute la période (exemple simplifié..)
        feature_cols = [c for c in df.columns if c.startswith(f"{col}_") or c in ["hour", "dayofweek"]]
        X_traffic = df[feature_cols]
        X_traffic_scaled = scalers_traffic[col].transform(X_traffic)
        df[f"predicted_{col}"] = models_traffic[col].predict(X_traffic_scaled)
    traffic_features = [f"predicted_{col}" for col in traffic_cols]
else:
    traffic_features = traffic_cols """
traffic_features = traffic_cols

In [44]:
# Get the created features names
feature_cols_air = (
    traffic_features +
    [c for c in df.columns if any(x in c for x in ["_lag", "_roll"]) and "air_quality" in c] +
    [c for c in df.columns if any(x in c for x in ["_lag", "_roll"]) and c.split("_")[0] in weather_cols] +
    ["hour", "dayofweek"]
)

Splitting the dataset into a training dataset and testing other.
Since I need continous time, I can not pick randomly to fill these two new datasets. I chose to take the first 80% of the timeframe as training, and the remaining part as testing. This has some flaws (for example, the seasons change), I will try other ways later.

In [45]:
# Split train/test
X = df[feature_cols_air]
y = df["target_air_quality"]
split_idx = int(len(df) * 0.8)
X_train, X_test = X.iloc[:split_idx], X.iloc[split_idx:]
y_train, y_test = y.iloc[:split_idx], y.iloc[split_idx:]


# Important: we removed some rows from X, we have to remove the corresponding ones from Y
y_test = y_test.loc[X_test.index]  # Have the same indexes as X_test
y_train = y_train.loc[X_train.index]

In [46]:
# Extended model search + summary for PM10 prediction
import time
import numpy as np
import pandas as pd

from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import RandomizedSearchCV, TimeSeriesSplit
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

# Models
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, HistGradientBoostingRegressor
from sklearn.linear_model import Ridge, ElasticNet
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR

# Optional: lightgbm if installed (recommended)
try:
    from lightgbm import LGBMRegressor
    has_lgb = True
except Exception:
    has_lgb = False
    print("lightgbm not available — LGBM will be skipped.")

# TimeSeries CV (prevents temporal leakage)
tscv = TimeSeriesSplit(n_splits=5)

# Models and parameter distributions (use pipeline param names: 'model__*')
models_and_params = {}

if has_lgb:
    models_and_params['LGBM'] = (
        LGBMRegressor(random_state=42),
        {
            'model__n_estimators': [100, 250, 500, 1000],
            'model__learning_rate': [0.01, 0.02, 0.05, 0.1],
            'model__max_depth': [-1, 3, 5, 7],
            'model__num_leaves': [31, 50, 100, 200],
            'model__min_child_samples': [5, 10, 20, 50],
            'model__subsample': [0.6, 0.8, 1.0],
            'model__colsample_bytree': [0.6, 0.8, 1.0],
        }
    )

models_and_params['RandomForest'] = (
    RandomForestRegressor(random_state=42),
    {
        'model__n_estimators': [100, 200, 500],
        'model__max_depth': [None, 10, 20, 30],
        'model__min_samples_split': [2, 5, 10],
        'model__min_samples_leaf': [1, 2, 4],
        'model__max_features': ['auto', 'sqrt', 'log2']
    }
)

models_and_params['HistGB'] = (
    HistGradientBoostingRegressor(random_state=42),
    {
        'model__learning_rate': [0.01, 0.05, 0.1],
        'model__max_iter': [100, 200, 500],
        'model__max_leaf_nodes': [31, 64, 128],
        'model__l2_regularization': [0.0, 0.1, 0.5]
    }
)

models_and_params['SklearnGB'] = (
    GradientBoostingRegressor(random_state=42),
    {
        'model__n_estimators': [100, 200, 500],
        'model__learning_rate': [0.01, 0.05, 0.1],
        'model__max_depth': [3, 5, 7],
        'model__subsample': [0.6, 0.8, 1.0]
    }
)

models_and_params['SVR'] = (
    SVR(),
    {
        'model__C': [0.1, 1, 10, 100],
        'model__epsilon': [0.01, 0.1, 0.5],
        'model__kernel': ['rbf', 'linear'],
        'model__gamma': ['scale', 'auto']
    }
)

models_and_params['KNN'] = (
    KNeighborsRegressor(),
    {
        'model__n_neighbors': [3, 5, 10, 20],
        'model__weights': ['uniform', 'distance'],
        'model__p': [1, 2]
    }
)

models_and_params['Ridge'] = (
    Ridge(random_state=42),
    {
        'model__alpha': [0.01, 0.1, 1.0, 10.0, 100.0]
    }
)

models_and_params['ElasticNet'] = (
    ElasticNet(random_state=42, max_iter=5000),
    {
        'model__alpha': [0.0001, 0.001, 0.01, 0.1, 1.0],
        'model__l1_ratio': [0.1, 0.3, 0.5, 0.7, 0.9]
    }
)

# Search configuration
n_iter = 25             # how many parameter settings to try in RandomizedSearchCV
n_jobs = -1             # parallel jobs
scoring = 'neg_mean_absolute_error'

results = []

for name, (estimator, param_dist) in models_and_params.items():
    print(f"\n=== Searching {name} ===")
    # Pipeline: scaling + model (scaling harmless for tree models and required for e.g. SVR)
    pipeline = Pipeline([
        ('scaler', StandardScaler()),
        ('model', estimator)
    ])

    search = RandomizedSearchCV(
        pipeline,
        param_distributions=param_dist,
        n_iter=n_iter,
        scoring=scoring,
        cv=tscv,
        verbose=1,
        random_state=42,
        n_jobs=n_jobs,
        return_train_score=False,
        refit=True
    )

    t0 = time.time()
    search.fit(X_train, y_train)
    fit_time = time.time() - t0

    best = search.best_estimator_
    best_params = search.best_params_
    best_cv_score = search.best_score_  # negative MAE (because scoring is neg_mae)

    # Predict on test set using the refit estimator (includes scaler)
    y_pred = best.predict(X_test)
    mae = mean_absolute_error(y_test, y_pred)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    r2 = r2_score(y_test, y_pred)

    # optionally keep CV std (if present)
    # find index of best in cv_results_ to get std
    try:
        best_index = int(np.argmin(search.cv_results_['mean_test_score'] * -1))  # hack to be safe
        cv_std = search.cv_results_['std_test_score'][best_index]
    except Exception:
        cv_std = np.nan

    print(f"{name} done — test MAE: {mae:.3f}, RMSE: {rmse:.3f}, R2: {r2:.3f}, cv_neg_mae: {best_cv_score:.3f}, fit_time: {fit_time:.1f}s")

    results.append({
        'model': name,
        'best_params': best_params,
        'cv_neg_mae': best_cv_score,
        'cv_std_neg_mae': cv_std,
        'mae': mae,
        'rmse': rmse,
        'r2': r2,
        'fit_time_s': fit_time,
        'estimator': best  # keep the fitted pipeline for later inspection
    })

# Build results DataFrame and sort by test MAE
results_df = pd.DataFrame(results).drop(columns=['estimator']).sort_values('mae').reset_index(drop=True)
pd.set_option('display.max_colwidth', 400)
print("\n--- Summary (sorted by test MAE) ---")
print(results_df[['model','mae','rmse','r2','cv_neg_mae','fit_time_s','best_params']])

# Save CSV for further inspection
results_df.to_csv("model_search_summary.csv", index=False)
print("\nSaved summary to model_search_summary.csv")

# If you want a quick visualization (plotly)
import plotly.express as px
fig = px.bar(results_df, x='model', y='mae', error_y='cv_std_neg_mae',
             title=f"Test MAE by model (lower is better) for {target_label} +{forecast_h}h",
             labels={'mae': 'MAE (test)', 'model': 'Model'})
fig.show()

# Plot predictions vs real for the best overall model (lowest test MAE)
best_overall = results[ np.argmin([r['mae'] for r in results]) ]['estimator']
y_best_pred = best_overall.predict(X_test)

import plotly.graph_objects as go
fig2 = go.Figure()
fig2.add_trace(go.Scatter(x=df["datetime_hour"].iloc[split_idx:], y=y_test, mode='lines', name='Real'))
fig2.add_trace(go.Scatter(x=df["datetime_hour"].iloc[split_idx:], y=y_best_pred, mode='lines', name='Best prediction', line=dict(dash='dash')))
fig2.update_layout(title=f"Best model ({results_df.loc[0,'model']}) — {target_label} predicted for +{forecast_h}h",
                   xaxis_title="Date", yaxis_title=f"{target_label} concentration")
fig2.show()

# Optional: print best model object and its parameters
print("\nBest overall model (by test MAE):", results_df.loc[0,'model'])
print("Best params:", results_df.loc[0,'best_params'])



=== Searching LGBM ===
Fitting 5 folds for each of 25 candidates, totalling 125 fits


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.016668 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 5748
[LightGBM] [Info] Number of data points in the train set: 973, number of used features: 50
[LightGBM] [Info] Start training from score 23.229188
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.012167 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 6237
[LightGBM] [Info] Number of data points in the train set: 1942, number of used features: 50
[LightGBM] [Info] Start training from score 21.712667
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.023152 seconds.
You can set `force_col_wise=true` to remove the overhead.
[Ligh


Best overall model (by test MAE): SVR
Best params: {'model__kernel': 'rbf', 'model__gamma': 'scale', 'model__epsilon': 0.01, 'model__C': 1}
